#### Point of this notebook is to relate galaxies to their closest respective filament (ID)
 - goal is to add filament ID's to total GAMA galaxy dataframe/catalog so that we can have filament information as well 

In [1]:
import numpy as np
import pandas as pd
from scipy import spatial #this is what we use to implement KDTree
import pickle

In [2]:
import sys  

sys.path.insert(0, '/Users/Daniel/Documents/Research Projects/Cosmic-Filaments/example_filaments') #change path to your local here (last part should be the same if cloned from GitHub)
import read_fils as rf #need this to import Janvi's package to work with DisPerSE files

sys.path.insert(0, '/Users/Daniel/Documents/Research Projects/Cosmic-Filaments/Filament_Metrics' ) #change here as well 
import fil_metrics.metric_functions as fm #need this to use fil metrics functions for manipulating dictionary of filaments 

pers5 = '/Users/Daniel/Documents/Research Projects/Cosmic-Filaments/GAMA_filaments/GAMA_tess.NDnet_s5.up.NDskl.S002.BRK.ASMB.rmO.rmB.a.NDskl'
pers4 = '/Users/Daniel/Documents/Research Projects/Cosmic-Filaments/GAMA_filaments/GAMA_tess.NDnet_s4.up.NDskl.S002.BRK.ASMB.rmO.rmB.a.NDskl'
pers2 = '/Users/Daniel/Documents/Research Projects/Cosmic-Filaments/GAMA_filaments/GAMA_tess.NDnet_s3.up.NDskl.S010.BRK.ASMB.rmO.rmB.a.NDskl'

skeleton_file_dm = pers4  # <-- CHANGE HERE to adjust persistance file being looked at 
filaments_dm = rf.ReadFilament(skeleton_file_dm) 
filament_dm_dict = filaments_dm.filament_dict
print(filament_dm_dict) 

header1, ANDSKEL

ndims, 3

Comments, #No comments (RB) (RB) (RB) (RB) (RB)

Bounding box, BBOX [-1436.7,-987.426,-78.1993] [1440.62,2098.18,156.865]

ncrit, 6928
nfils, 7340
Reading data fields:
CP field: persistence_ratio

CP field: persistence_nsigmas

CP field: persistence

CP field: robustness_ratio

CP field: robustness

CP field: persistence_pair

CP field: parent_index

CP field: parent_log_index

CP field: log_field_value

CP field: field_value

CP field: cell

Filament field: field_value

Filament field: orientation

Filament field: cell

Filament field: log_field_value

Filament field: type

Filament field: robustness

Filament field: robustness_ratio

Reading filaments took 0.09 secs.
{'ncrit': 6928, 'critical_points': [{'cp_idx': 3.0, 'px': -474.964, 'py': -316.167, 'pz': -3.36726, 'pair_ID': 1352.0, 'boundary': 0.0, 'nfil': 2, 'destID,filID': [[1, 0], [2, 1]], 'Field Vals': [1263.43, 5.35172, 39.39744, 7707.566, 22.16735, 1352.0, 300.0, 300.0, 1.595812, 39.42865, 11556.0]

In [3]:
#separate 'filaments' and 'critical_points' dictionaries (each is now a list of dictionaries)
fils = filament_dm_dict['filaments'] 
crit_points = filament_dm_dict['critical_points'] 
#number of filaments
nfils = filament_dm_dict['nfils'] ; ncrit = filament_dm_dict['ncrit']
print("# of filaments: ",nfils,"\n","# of critical points :",ncrit)

# of filaments:  7340 
 # of critical points : 6928


In [4]:
# CREATE DATAFRAME OF FILAMENT POINTS WHILE KEEPING FILAMENT ID -- INCLUDING SEGMENTS
df = pd.DataFrame()
for i in range(filament_dm_dict['nfils']):
    p = np.array(filament_dm_dict['filaments'][i]['px,py,pz'])
    p = np.hstack([p[:-1],p[1:]]) #removing final element of first parts and first element of second (to address 'picket fence' problem)
    p = pd.DataFrame(p,columns = ['px', 'py', 'pz','px2','py2','pz2']) #adding the second pair of points (the 'end' part of the extremity)
    p['Filament ID'] = i
    df = pd.concat([df, p])
df 

px       py        pz      px2      py2       pz2  Filament ID
0  -474.964 -316.167  -3.36726 -474.767 -315.979  -3.45685            0
1  -474.767 -315.979  -3.45685 -474.476 -315.625  -3.66815            0
2  -474.476 -315.625  -3.66815 -474.099 -315.196  -3.91581            0
3  -474.099 -315.196  -3.91581 -473.644 -314.865  -4.05575            0
4  -473.644 -314.865  -4.05575 -473.134 -314.627  -4.05447            0
..      ...      ...       ...      ...      ...       ...          ...
3  -443.991 -317.901 -16.19660 -443.361 -318.762 -15.77110         7338
0  -775.965  645.095 -26.83350 -773.344  646.519 -23.22260         7339
1  -773.344  646.519 -23.22260 -770.871  648.032 -20.45670         7339
2  -770.871  648.032 -20.45670 -768.352  649.882 -18.76000         7339
3  -768.352  649.882 -18.76000 -765.503  651.824 -17.12840         7339

[36307 rows x 7 columns]

In [5]:
# array of dataframe above
filarray = np.array(df) 
filarray[0] #array of filaments where each element contains the two pair of points that constitute a segment of the filament and the filament ID

array([-474.964  , -316.167  ,   -3.36726, -474.767  , -315.979  ,
         -3.45685,    0.     ])

In [6]:
#import galaxies 
dfgalaxies = pd.read_csv('/Users/Daniel/Documents/Research Projects/Cosmic-Filaments/Gama_Galaxies/Gama_Catalog_Euclidean_copy.txt', delimiter=' ')
dfgalaxies

px          py         pz   logmstar
0       -216.625210   22.745292   2.740837   9.076030
1      -1224.886159  128.248150  15.175059  10.979200
2       -895.469883   92.526596  10.353321  10.791600
3      -1209.953065  124.842693  17.067738  11.119700
4       -323.199357   33.861492   3.776433   9.012390
...             ...         ...        ...        ...
113153  -871.610163 -719.567317  23.754061  10.410600
113154  -687.527336 -580.637147  16.334981   9.689020
113155    -0.215265   -0.154865   0.007690   0.464692
113156    -1.102929   -1.020451   0.040281   1.253310
113157  -508.890334   -6.817909  -1.111927   9.825090

[113158 rows x 4 columns]

In [7]:
galaxies = np.array(dfgalaxies.iloc[:,:-1]) #removes logmstar and makes into array 
galaxies

array([[-2.16625210e+02,  2.27452918e+01,  2.74083730e+00],
       [-1.22488616e+03,  1.28248150e+02,  1.51750591e+01],
       [-8.95469883e+02,  9.25265956e+01,  1.03533213e+01],
       ...,
       [-2.15265246e-01, -1.54865181e-01,  7.69026908e-03],
       [-1.10292917e+00, -1.02045078e+00,  4.02806750e-02],
       [-5.08890334e+02, -6.81790904e+00, -1.11192676e+00]])

### KD Tree implementation (outside of loop)

In [8]:
#index filament segment pairs array here 
segment1 = filarray[:,:-4]
segment1 #corresponds to the first three columns of the array (which are the first/beginning extremities of each filament segment)

array([[-474.964  , -316.167  ,   -3.36726],
       [-474.767  , -315.979  ,   -3.45685],
       [-474.476  , -315.625  ,   -3.66815],
       ...,
       [-773.344  ,  646.519  ,  -23.2226 ],
       [-770.871  ,  648.032  ,  -20.4567 ],
       [-768.352  ,  649.882  ,  -18.76   ]])

In [9]:
segment1.shape

(36307, 3)

In [10]:
#actual KDTree implementation is here 
knn = 10 #decide here how many nearest neighbors you want (will decide how many indeces are returned for each galaxy)

distance, index = spatial.KDTree(segment1).query(galaxies, k=knn) 
index #index of single closest filament_array point for each galaxy

array([[ 2062,  2054, 16460, ..., 16423,  2052,  2064],
       [17695, 17696, 17694, ..., 33581, 33583, 17724],
       [23266, 23265, 23269, ..., 29233, 33567, 23268],
       ...,
       [11757, 11756, 10607, ..., 10592, 11876, 11884],
       [ 1492,  1491,  1376, ...,  1483,  1484,  1374],
       [29187, 29186, 29182, ..., 29181, 29175, 29207]])

In [11]:
df.iloc[2062]

px            -216.01300
py              20.99770
pz              -6.12680
px2           -212.73200
py2             19.23320
pz2             -7.21457
Filament ID    383.00000
Name: 0, dtype: float64

In [12]:
testpoint1 = df.iloc[2062][:-4] #this should be the closest segment (with a distance of 9.0589) to first galaxy
testpoint1

px   -216.0130
py     20.9977
pz     -6.1268
Name: 0, dtype: float64

In [13]:
#check distance 
np.linalg.norm(galaxies[0] - testpoint1) #voila! It's correct and the 'index' output gives the indices of the segment ID (double voila!!)

9.058911059939476

In [14]:
distance[0] #returns array of 10 closest fil segment extremity distances for FIRST galaxy

array([ 9.05891106, 10.43826933, 11.16331334, 11.25175579, 12.41400632,
       12.50820873, 12.79584699, 13.46362867, 13.49741058, 13.57628566])

In [15]:
print(len(index[0]),"\n", len(index))

10 
 113158


### Galaxy-Filament Distance (tweaked) to return closest galaxy-fil distances AND filament ID assocaited to each closest galaxy

In [16]:
def galfildist(galaxies, filament_points, KDTindex): #KDTindex is where you insert array of indices from KDTree function above
    '''Finds closest distance between an array of galaxies and 
        an array of filament points. The filament_points array must be 
        segmented so that the first element corresponds to the first pair of points
        (which correspond to the first two points of a filament segment's extremity).
        This code is optimized and intended to be used AFTER implementing a KDTree.
        KDTindex must correspond to the index array that comes out of using KDTree.'''
    shortest_distances = np.zeros(len(galaxies)) 
    indices = np.zeros(len(galaxies)) ## <---------- ADDED TO SAVE INDICES
    for h in range(len(galaxies)):
        distances = np.zeros(len(KDTindex[0])) #distances should be same size as number of knn checked in KDTree 
        workingarray = filament_points[KDTindex[h]]
        for i in range(len(workingarray)): #nested loop but only for the number of knn there are 
            #A corresponds to first extremity point of segment, B to the second extremity point
            A = workingarray[i,:-4] ; B = workingarray[i,3:-1] ; AB = B - A ; AG = galaxies[h] - A 
            # TRY HERE TO SAVE INDEX

            u = AB / np.linalg.norm(AB) #creation of unit vector 
            #Statement checks 
            if np.dot(AG, u) < 0:
                distances[i] = np.linalg.norm(galaxies[h] - A)
                indices[h] = filarray[KDTindex[h][i]][-1]
                continue

            elif np.dot(AG, u) > np.linalg.norm(AB):
                distances[i] = np.linalg.norm(galaxies[h] - B)
                indices[h] = filarray[KDTindex[h][i]][-1]
                continue
            
            elif np.dot(AG, u) < np.linalg.norm(AB):
                distances[i] = np.linalg.norm((np.cross((A-B), (A-galaxies[h])))) / (np.linalg.norm(galaxies[h]-B))
                indices[h] = filarray[KDTindex[h][i]][-1]
                continue

        shortest_distances[h] = np.min(distances)
    
    return shortest_distances, indices
            

In [17]:
gf_distances = galfildist(galaxies, filarray, index)

In [18]:
gf_distances[0].shape #array of shortest distances

(113158,)

In [19]:
gf_distances[1] # working array --> filament_points[KDTree_Index[h]]

array([ 383., 3444., 4604., ..., 2256.,  254., 5820.])

In [20]:
gf_distances[1] #should be the same as testpoint1

array([ 383., 3444., 4604., ..., 2256.,  254., 5820.])

In [21]:
gf_distances[1].shape

(113158,)

In [22]:
gf_distances[1] # these should be the filament ID's that each galaxy is closest to 

array([ 383., 3444., 4604., ..., 2256.,  254., 5820.])

In [23]:
filarray[0]

array([-474.964  , -316.167  ,   -3.36726, -474.767  , -315.979  ,
         -3.45685,    0.     ])

In [24]:
np.unique(gf_distances[1]).shape # how many unique filament IDs there are

(7254,)

In [25]:
gf_distances

(array([4.99639705e+00, 2.94516008e+01, 3.83597328e+00, ...,
        8.42312403e-03, 4.36343240e-02, 1.60760379e+00]),
 array([ 383., 3444., 4604., ..., 2256.,  254., 5820.]))

In [26]:
#save galaxy - filament distances 
#with open('/Users/Daniel/Documents/Research Projects/Cosmic-Filaments/Pickles/pers4_galfil_IDS.pkl', 'wb') as f: 
#    pickle.dump(gf_distances[1], f)